# Demonstration of k-means and hierarchical clustering
Information on the iris data here: https://en.wikipedia.org/wiki/Iris_flower_data_set

Information on the sklearn machine learning library here: http://scikit-learn.org/

We evaluate the different clustering methods using the [adjusted rand index](http://scikit-learn.org/stable/modules/generated/sklearn.metrics.adjusted_rand_score.html), a measure between 0 and 1 with 1 denoting a perfect agreement with the true labels. This is only possible when class labels are known.

In [8]:
# from matplotlib import pyplot as plt
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import visualisation
import clustering
# use PCA from sklearn
from sklearn.decomposition import PCA
# plotly
import plotly
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=False)
# use seaborn plotting style defaults
doInteractive = True
def interactivePlots(fig, axes):
    # helper function to decide to use plotly interactive plots or not
    if(doInteractive):
        plotly.offline.iplot_mpl(fig, show_link=False, strip_style=True) # offline ipython notebook 

### Import Iris dataset from sklearn and put into a pandas DataFrame

In [9]:
# Iris data
from sklearn import datasets
data = datasets.load_iris()
irislabels = np.array(['setosa']*50 + ['versicolor']*50 + ['virginica']*50)
irisdata = pd.DataFrame(data.data, columns = ['Sepal length',
                                              'Sepal width','Petal length','Petal width'], index = irislabels)

###  Data summary: rows are samples, columns are features

In [10]:
print('data shape\n', irisdata.shape)
irisdata.head()

data shape
 (150, 4)


Sepal length  Sepal width  Petal length  Petal width
setosa           5.1          3.5           1.4          0.2
setosa           4.9          3.0           1.4          0.2
setosa           4.7          3.2           1.3          0.2
setosa           4.6          3.1           1.5          0.2
setosa           5.0          3.6           1.4          0.2

### Calculate PCA so that we can visualise the clusters of data in 2D
We will only use PCA to help visualise the data, it plays no role in any of the clustering algorithms used here

In [11]:
Wt, scores, fracs = visualisation.do_pca(irisdata)
scores = scores/abs(scores).max().max()

### Run the k-means algorithm

In [12]:
from sklearn.cluster import KMeans
kmeans = KMeans(n_clusters=3, random_state=0).fit(irisdata.values)

### Return the cluster labels for each data item

In [13]:
kmeanslabels = kmeans.labels_
print (kmeanslabels)

[1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1
 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 2 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 2 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 2 0 2 2 2 2 0 2 2 2 2
 2 2 0 0 2 2 2 2 0 2 0 2 0 2 2 0 0 2 2 2 2 2 0 2 2 2 2 0 2 2 2 0 2 2 2 0 2
 2 0]


### Compare cluster labels and class labels on the PCA projection
Note that the clustering was not done in the PCA space, it was done in the original 4-dimensional data space

What does the Adjusted Rand Index tell us here? 

In [14]:
from __future__ import print_function
from ipywidgets import interact, interactive, fixed
import ipywidgets as widgets
from sklearn.metrics import adjusted_rand_score
def plotinteractPCA(feature='kmeans', XaxisPC=1, YaxisPC=2):
    traceGene = list()
    
    if(feature == 'class' or feature == 'kmeans'):
        labelsPlot = np.unique(kmeanslabels)
        labelsAll = kmeanslabels
        if(feature == 'class'):
            labelsPlot = np.unique(irislabels)
            labelsAll = irislabels
        ari = adjusted_rand_score(labelsAll, irislabels)
        for lbl in labelsPlot:
            traceGene.append(go.Scatter(
                x = scores[labelsAll==lbl].iloc[:,XaxisPC-1],
                y = scores[labelsAll==lbl].iloc[:,YaxisPC-1],
                mode='markers',
                name = lbl,
                text = lbl
                ))
        layout = go.Layout(showlegend=True, title='Interactive PCA plot, AdjRand Index %.2f' % ari ,
                       annotations=list(), legend={'orientation': 'h'})
    else:
        traceGene.append(go.Scatter(
            x = scores.iloc[:,XaxisPC],
            y = scores.iloc[:,YaxisPC],
            mode='markers',
            marker = {'color': irisdata[feature].values, 'size': 10, 'colorscale': 'Viridis',
                      'colorbar':{'title': 'expression'}},
            text = irislabels,
            name = 'Expression'
            ))
        layout = go.Layout(showlegend=True, title='Interactive PCA plot' ,
                       annotations=list(), legend={'orientation': 'h'})
    
    fig = go.Figure(data=traceGene, layout=layout)
    iplot(fig)
_=interact(plotinteractPCA, feature=['kmeans', 'class']+list(irisdata.columns.values),XaxisPC=(1, 4), YaxisPC=(2, 4))

interactive(children=(Dropdown(description='feature', options=('kmeans', 'class', 'Sepal length', 'Sepal width', 'Petal length', 'Petal width'), value='kmeans'), IntSlider(value=1, description='XaxisPC', max=4, min=1), IntSlider(value=2, description='YaxisPC', max=4, min=2), Output()), _dom_classes=('widget-interact',))

## Hierarchical clustering
For a very nice tutorial see [this page](https://joernhees.de/blog/2015/08/26/scipy-hierarchical-clustering-and-dendrogram-tutorial/).

In [16]:
from scipy.cluster.hierarchy import dendrogram, linkage
np.set_printoptions(precision=5, suppress=True)  # suppress scientific float notation
%matplotlib inline

In [17]:
# generate the linkage matrix
X = irisdata.values
print('Shape', X.shape)
Z = linkage(X, method='ward', metric='euclidean')
print(Z)

Shape (150, 4)
[[   9.        34.         0.         2.     ]
 [  37.       150.         0.         3.     ]
 [ 101.       142.         0.         2.     ]
 [   7.        39.         0.1        2.     ]
 [   0.        17.         0.1        2.     ]
 [ 128.       132.         0.1        2.     ]
 [  10.        48.         0.1        2.     ]
 [  19.        21.         0.14142    2.     ]
 [  29.        30.         0.14142    2.     ]
 [  57.        93.         0.14142    2.     ]
 [  80.        81.         0.14142    2.     ]
 [ 116.       137.         0.14142    2.     ]
 [   8.        38.         0.14142    2.     ]
 [   3.        47.         0.14142    2.     ]
 [  27.        28.         0.14142    2.     ]
 [  82.        92.         0.14142    2.     ]
 [  95.        96.         0.14142    2.     ]
 [ 127.       138.         0.14142    2.     ]
 [   1.        45.         0.14142    2.     ]
 [  63.        91.         0.14142    2.     ]
 [  65.        75.         0.14142    2.     

### For an explanation of other linkage methods and metrics see [this page](https://docs.scipy.org/doc/scipy-0.18.1/reference/generated/scipy.cluster.hierarchy.linkage.html#scipy.cluster.hierarchy.linkage)
### For an explanation of difference distance metrics see [here](https://docs.scipy.org/doc/scipy/reference/generated/scipy.spatial.distance.pdist.html).

### Let us now look at the linkage matrix:

In [18]:
Z[:5,:]

array([[   9. ,   34. ,    0. ,    2. ],
       [  37. ,  150. ,    0. ,    3. ],
       [ 101. ,  142. ,    0. ,    2. ],
       [   7. ,   39. ,    0.1,    2. ],
       [   0. ,   17. ,    0.1,    2. ]])

### The last column gives you the cluster size for each step of the algorithm. We see already in the second step a cluster of  three points.
The first two columns are the indices of the points. So in the first step point 9 and point 34 are merged into a single cluster. All indices over the data size, in this case we have 150 points, denote a merge of an existing cluster with another cluster/point. In the second row we show points 37 and 150 merge - but point 150 does not exists because we have data indices 0-149 - remember in python we have 0-based counting! So this denotes the merging of point 37 with a new 'point' 150 which represents the cluster containing 9 and 34. Every time a cluster is formed it is given the next index, so the cluster containing 9, 34 and 37 will be numbered 151 and so on. 

### Now let us plot a dendogram summarising the clustering.
For a particular cutoff a specific number of clusters is defined. We show these on the PCA plot below the dendogram.

In [21]:
def plotinteractHierarchicalClustering(method='ward', metric='euclidean', XaxisPC=1, YaxisPC=2,
                                      distanceThreshold=0.3):
    if(method in ['‘centroid’, ‘median’,‘ward’'] and metric != 'euclidean'):
        raise NameError('Methods ‘centroid’, ‘median’ and ‘ward’ are correctly defined only if Euclidean pairwise metric is used.') 
    
    X = irisdata.values.copy()
    Z = linkage(X, method=method, metric=metric)
    Z[:, 2] = Z[:, 2] / Z[:, 2].max()  # distance in [0, 1]
    plt.figure(figsize=(25, 10))
    plt.title('Hierarchical Clustering Dendrogram')
    plt.xlabel('sample index')
    plt.ylabel('distance')
    dendrogram(
        Z,
        leaf_rotation=90.,  # rotates the x axis labels
        leaf_font_size=8.,  # font size for the x axis labels
    )
    ax = plt.gca()
    ax.tick_params(axis='y', which='major', labelsize=20)  
    ax.set_ylabel('Distance', fontsize=20)  
    ax.set_xlabel('Sample Index', fontsize=20)  
    ax.set_title('Hierarchical Clustering Dendrogram', fontsize=20)  
    plt.axhline(y=distanceThreshold, c='k')
    plt.show()
    
    # do clustering plot
    traceGene = list()
    cid = clustering.GetClusters(Z.copy(), X.copy(), distanceThreshold)
    labelsPlot = np.unique(cid)
    labelsAll = cid
    ari = adjusted_rand_score(labelsAll, irislabels)
    for lbl in labelsPlot:
        traceGene.append(go.Scatter(
            x = scores[labelsAll==lbl].iloc[:,XaxisPC-1],
            y = scores[labelsAll==lbl].iloc[:,YaxisPC-1],
            mode='markers',
            name = lbl,
            text = lbl
            ))
    layout = go.Layout(showlegend=True, title='Threshold=%.2f, Number of clusters=%g, AdjRand Index %.2f' % 
                       (distanceThreshold, labelsPlot.size, ari),
                       annotations=list(), legend={'orientation': 'h'})
    fig = go.Figure(data=traceGene, layout=layout)
    iplot(fig)
_=interact(plotinteractHierarchicalClustering, method=['ward', 'single', 'complete', 'average', 'weighted', 'centroid', 'median'],
          metric=['euclidean', 'minkowski', 'cityblock', 'seuclidean', 'sqeuclidean', 'cosine', 'correlation', 'hamming', 
                 'jaccard', 'chebyshev', 'canberra', 'braycurtis', 'mahalanobis', 'wminkowski'],
          XaxisPC=(1, 4), YaxisPC=(2, 4), distanceThreshold=(0.0,1.0,0.01))

interactive(children=(Dropdown(description='method', options=('ward', 'single', 'complete', 'average', 'weighted', 'centroid', 'median'), value='ward'), Dropdown(description='metric', options=('euclidean', 'minkowski', 'cityblock', 'seuclidean', 'sqeuclidean', 'cosine', 'correlation', 'hamming', 'jaccard', 'chebyshev', 'canberra', 'braycurtis', 'mahalanobis', 'wminkowski'), value='euclidean'), IntSlider(value=1, description='XaxisPC', max=4, min=1), IntSlider(value=2, description='YaxisPC', max=4, min=2), FloatSlider(value=0.3, description='distanceThreshold', max=1.0, step=0.01), Output()), _dom_classes=('widget-interact',))